In [ ]:
# Imports
import torch
import torch.nn as nn  # all NN modules
import torch.nn.functional as F  # RElu, Tanh, ...
import torch.optim as optim  # SGD, Adam, ...
import torchvision.datasets as datasets  # MNIST dataset
import torchvision.transforms as transforms  # Tranformations on dataset
from torch.utils.data import DataLoader  # Dataset management and minibatches
from torch.utils.tensorboard import SummaryWriter

# TODO: create a simple CNN
class CNN(nn.Module):
    def __init__(self, in_channel=1, num_classes=10):
        super(CNN, self).__init__()
        self.conv1 = nn.Conv2d(
            in_channels=in_channel,
            out_channels=8,
            kernel_size=(3, 3),
            stride=(1, 1),
            padding=(1, 1),
        )  # same convolution
        self.pool = nn.MaxPool2d(kernel_size=(2, 2), stride=(2, 2))
        self.conv2 = nn.Conv2d(
            in_channels=8,
            out_channels=16,
            kernel_size=(3, 3),
            stride=(1, 1),
            padding=(1, 1),
        )  # same convolution
        self.fc1 = nn.Linear(16 * 7 * 7, num_classes)

    def forward(self, x):
        x = F.relu(self.conv1(x))
        x = self.pool(x)
        x = F.relu(self.conv2(x))
        x = self.pool(x)
        x = x.reshape(x.shape[0], -1)
        x = self.fc1(x)
        return x


# Set device
if torch.cuda.is_available():
    device = "gpu"
elif torch.has_mps:
    device = "mps"
else:
    device = "cpu"
device = torch.device(device)
print(device)

# Hyper parameters
in_channel = 1
num_classes = 10
learning_rate = 0.001
batch_size = 64
num_epochs = 5

# Load data
train_dataset = datasets.MNIST(
    root="dataset/", train=True, transform=transforms.ToTensor(), download=True
)
test_dataset = datasets.MNIST(
    root="dataset/", train=False, transform=transforms.ToTensor(), download=True
)
train_loader = DataLoader(dataset=train_dataset, batch_size=batch_size, shuffle=True)
test_loader = DataLoader(dataset=test_dataset, batch_size=batch_size, shuffle=True)

# Initialize network
model = CNN(in_channel=in_channel, num_classes=num_classes).to(device)

# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=learning_rate)
writer = SummaryWriter(f'runs/MNIST/tryingout_tensorboard')

step = 0
# Train network
for epoch in range(num_epochs):  # epoch
    losses = []
    accuracies = []
    for batch_idx, (data, targets) in enumerate(train_loader):  # batch
        # Get data to CUDA if possible
        data = data.to(device=device)
        targets = targets.to(device=device)

        # Forward
        scores = model(data)
        loss = criterion(scores, targets)
        losses.append(loss.item())

        # Backward
        optimizer.zero_grad()
        loss.backward()

        # Gradient descent or Adam step
        optimizer.step()  # update the weights

        # Calculate running training accuracy
        _, predictions = scores.max(dim=1)
        num_correct = (predictions == targets).sum()
        num_samples = predictions.size(0)
        running_training_acc = float(num_correct) / float(data.shape[0])
        print(f"Got {num_correct} / {num_samples} with accuracy {float(num_correct) / float(num_samples) * 100:.2f}")

        writer.add_scalar('Training loss', loss, global_step=step)
        writer.add_scalar('Training accuracy', running_training_acc, global_step=step)
        step += 1

# Check accuracy on training and test to see how good our moodel is
def check_accuracy(loader, model):
    if loader.dataset.train:
        print("Checking accuracy on training data")
    else:
        print("Checking accuracy on test data")
    num_correct = 0
    num_samples = 0
    model.eval()

    with torch.no_grad():
        for x, y in loader:
            x = x.to(device=device)
            y = y.to(device=device)

            scores = model(x)
            # 64x10
            _, predictions = scores.max(dim=1)
            num_correct += (predictions == y).sum()
            num_samples += predictions.size(0)
        print(
            f"Got {num_correct} / {num_samples} with accuracy {float(num_correct) / float(num_samples) * 100:.2f}"
        )

    model.train()
    return num_correct / num_samples


check_accuracy(train_loader, model)
check_accuracy(test_loader, model)


# Important Note about `run` folder:

Empty `run` folder before running the second block of code.

In [ ]:
# Imports
import torch
import torch.nn as nn  # all NN modules
import torch.nn.functional as F  # RElu, Tanh, ...
import torch.optim as optim  # SGD, Adam, ...
import torchvision.datasets as datasets  # MNIST dataset
import torchvision.transforms as transforms  # Tranformations on dataset
from torch.utils.data import DataLoader  # Dataset management and minibatches
from torch.utils.tensorboard import SummaryWriter

# TODO: create a simple CNN
class CNN(nn.Module):
    def __init__(self, in_channel=1, num_classes=10):
        super(CNN, self).__init__()
        self.conv1 = nn.Conv2d(
            in_channels=in_channel,
            out_channels=8,
            kernel_size=(3, 3),
            stride=(1, 1),
            padding=(1, 1),
        )  # same convolution
        self.pool = nn.MaxPool2d(kernel_size=(2, 2), stride=(2, 2))
        self.conv2 = nn.Conv2d(
            in_channels=8,
            out_channels=16,
            kernel_size=(3, 3),
            stride=(1, 1),
            padding=(1, 1),
        )  # same convolution
        self.fc1 = nn.Linear(16 * 7 * 7, num_classes)

    def forward(self, x):
        x = F.relu(self.conv1(x))
        x = self.pool(x)
        x = F.relu(self.conv2(x))
        x = self.pool(x)
        x = x.reshape(x.shape[0], -1)
        x = self.fc1(x)
        return x


# Set device
if torch.cuda.is_available():
    device = "gpu"
elif torch.has_mps:
    device = "mps"
else:
    device = "cpu"
device = torch.device(device)
print(device)

# Hyper parameters
in_channel = 1
num_classes = 10
num_epochs = 1

# Load data
train_dataset = datasets.MNIST(
    root="dataset/", train=True, transform=transforms.ToTensor(), download=True
)
test_dataset = datasets.MNIST(
    root="dataset/", train=False, transform=transforms.ToTensor(), download=True
)

batch_sizes = [2, 64, 1024]
learning_rates = [0.1, 0.01, 0.001, 0.0001]

for batch_size in batch_sizes:
    for learning_rate in learning_rates:

        # Initialize network
        model = CNN(in_channel=in_channel, num_classes=num_classes).to(device)

        train_loader = DataLoader(dataset=train_dataset, batch_size=batch_size, shuffle=True)
        test_loader = DataLoader(dataset=test_dataset, batch_size=batch_size, shuffle=True)

        # Loss and optimizer
        criterion = nn.CrossEntropyLoss()
        optimizer = optim.Adam(model.parameters(), lr=learning_rate)
        writer = SummaryWriter(f'runs/MNIST/MiniBatchSize {batch_size} LR {learning_rate}')

        step = 0
        # Train network
        for epoch in range(num_epochs):  # epoch
            losses = []
            accuracies = []
            for batch_idx, (data, targets) in enumerate(train_loader):  # batch
                # Get data to CUDA if possible
                data = data.to(device=device)
                targets = targets.to(device=device)

                # Forward
                scores = model(data)
                loss = criterion(scores, targets)
                losses.append(loss.item())

                # Backward
                optimizer.zero_grad()
                loss.backward()

                # Gradient descent or Adam step
                optimizer.step()  # update the weights

                # Calculate running training accuracy
                _, predictions = scores.max(dim=1)
                num_correct = (predictions == targets).sum()
                num_samples = predictions.size(0)
                running_training_acc = float(num_correct) / float(data.shape[0])
                print(f"Got {num_correct} / {num_samples} with accuracy {float(num_correct) / float(num_samples) * 100:.2f}")

                writer.add_scalar('Training loss', loss, global_step=step)
                writer.add_scalar('Training accuracy', running_training_acc, global_step=step)
                step += 1

# Check accuracy on training and test to see how good our moodel is
def check_accuracy(loader, model):
    if loader.dataset.train:
        print("Checking accuracy on training data")
    else:
        print("Checking accuracy on test data")
    num_correct = 0
    num_samples = 0
    model.eval()

    with torch.no_grad():
        for x, y in loader:
            x = x.to(device=device)
            y = y.to(device=device)

            scores = model(x)
            # 64x10
            _, predictions = scores.max(dim=1)
            num_correct += (predictions == y).sum()
            num_samples += predictions.size(0)
        print(
            f"Got {num_correct} / {num_samples} with accuracy {float(num_correct) / float(num_samples) * 100:.2f}"
        )

    model.train()
    return num_correct / num_samples


check_accuracy(train_loader, model)
check_accuracy(test_loader, model)


# Improve above for better visualization 

In [1]:
# Imports
import torch
import torch.nn as nn  # all NN modules
import torch.nn.functional as F  # RElu, Tanh, ...
import torch.optim as optim  # SGD, Adam, ...
import torchvision.datasets as datasets  # MNIST dataset
import torchvision.transforms as transforms  # Tranformations on dataset
from torch.utils.data import DataLoader  # Dataset management and minibatches
from torch.utils.tensorboard import SummaryWriter

# TODO: create a simple CNN
class CNN(nn.Module):
    def __init__(self, in_channel=1, num_classes=10):
        super(CNN, self).__init__()
        self.conv1 = nn.Conv2d(
            in_channels=in_channel,
            out_channels=8,
            kernel_size=(3, 3),
            stride=(1, 1),
            padding=(1, 1),
        )  # same convolution
        self.pool = nn.MaxPool2d(kernel_size=(2, 2), stride=(2, 2))
        self.conv2 = nn.Conv2d(
            in_channels=8,
            out_channels=16,
            kernel_size=(3, 3),
            stride=(1, 1),
            padding=(1, 1),
        )  # same convolution
        self.fc1 = nn.Linear(16 * 7 * 7, num_classes)

    def forward(self, x):
        x = F.relu(self.conv1(x))
        x = self.pool(x)
        x = F.relu(self.conv2(x))
        x = self.pool(x)
        x = x.reshape(x.shape[0], -1)
        x = self.fc1(x)
        return x


# Set device
if torch.cuda.is_available():
    device = "gpu"
elif torch.has_mps:
    device = "mps"
else:
    device = "cpu"
device = torch.device(device)
print(device)

# Hyper parameters
in_channel = 1
num_classes = 10
num_epochs = 1

# Load data
train_dataset = datasets.MNIST(
    root="dataset/", train=True, transform=transforms.ToTensor(), download=True
)
test_dataset = datasets.MNIST(
    root="dataset/", train=False, transform=transforms.ToTensor(), download=True
)

batch_sizes = [2, 64, 1024]
learning_rates = [0.1, 0.01, 0.001, 0.0001]

for batch_size in batch_sizes:
    for learning_rate in learning_rates:

        # Initialize network
        model = CNN(in_channel=in_channel, num_classes=num_classes).to(device)

        train_loader = DataLoader(dataset=train_dataset, batch_size=batch_size, shuffle=True)
        test_loader = DataLoader(dataset=test_dataset, batch_size=batch_size, shuffle=True)

        # Loss and optimizer
        criterion = nn.CrossEntropyLoss()
        optimizer = optim.Adam(model.parameters(), lr=learning_rate)
        writer = SummaryWriter(f'runs/MNIST/MiniBatchSize {batch_size} LR {learning_rate}')

        step = 0
        # Train network
        for epoch in range(num_epochs):  # epoch
            losses = []
            accuracies = []
            for batch_idx, (data, targets) in enumerate(train_loader):  # batch
                # Get data to CUDA if possible
                data = data.to(device=device)
                targets = targets.to(device=device)

                # Forward
                scores = model(data)
                loss = criterion(scores, targets)
                losses.append(loss.item())

                # Backward
                optimizer.zero_grad()
                loss.backward()

                # Gradient descent or Adam step
                optimizer.step()  # update the weights

                # Calculate running training accuracy
                _, predictions = scores.max(dim=1)
                num_correct = (predictions == targets).sum()
                num_samples = predictions.size(0)
                running_training_acc = float(num_correct) / float(data.shape[0])
                accuracies.append(running_training_acc)
                print(f"Got {num_correct} / {num_samples} with accuracy {float(num_correct) / float(num_samples) * 100:.2f}")

                writer.add_scalar('Training loss', loss, global_step=step)
                writer.add_scalar('Training accuracy', running_training_acc, global_step=step)
                step += 1
            writer.add_hparams({'lr':learning_rate, 'bsize':batch_size}, {'accuracy':sum(accuracies)/len(accuracies), 'Loss':sum(losses)/len(losses)})

# Check accuracy on training and test to see how good our moodel is
def check_accuracy(loader, model):
    if loader.dataset.train:
        print("Checking accuracy on training data")
    else:
        print("Checking accuracy on test data")
    num_correct = 0
    num_samples = 0
    model.eval()

    with torch.no_grad():
        for x, y in loader:
            x = x.to(device=device)
            y = y.to(device=device)

            scores = model(x)
            # 64x10
            _, predictions = scores.max(dim=1)
            num_correct += (predictions == y).sum()
            num_samples += predictions.size(0)
        print(
            f"Got {num_correct} / {num_samples} with accuracy {float(num_correct) / float(num_samples) * 100:.2f}"
        )

    model.train()
    return num_correct / num_samples


check_accuracy(train_loader, model)
check_accuracy(test_loader, model)


mps
Got 0 / 2 with accuracy 0.00
Got 2 / 2 with accuracy 100.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 1 / 2 with accuracy 50.00
Got 1 / 2 with accuracy 50.00
Got 1 / 2 with accuracy 50.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 1 / 2 with accuracy 50.00
Got 1 / 2 with accuracy 50.00
Got 0 / 2 with accuracy 0.00
Got 1 / 2 with accuracy 50.00
Got 1 / 2 with accuracy 50.00
Got 1 / 2 with accuracy 50.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00
Got 0 / 2 with accuracy 0.00


/Users/amirhosseindaraie/miniconda3/envs/torch-nightly/lib/python3.8/site-packages/torch/_tensor_str.py:103: UserWarning: The operator 'aten::bitwise_and.Tensor_out' is not currently supported on the MPS backend and will fall back to run on the CPU. This may have performance implications. (Triggered internally at /Users/runner/work/pytorch/pytorch/pytorch/aten/src/ATen/mps/MPSFallback.mm:11.)
  nonzero_finite_vals = torch.masked_select(tensor_view, torch.isfinite(tensor_view) & tensor_view.ne(0))


tensor(0., device='mps:0')